# Лабораторная работа № 8

### Выполнил: Федоров К.С.
### Группа: Б8403а

In [212]:
import numpy as np
import pandas as pd
import scipy as sp
import matplotlib.pyplot as plt
import plotly.offline as py
import plotly.graph_objs as go
py.init_notebook_mode(connected=True)
from scipy.stats import multivariate_normal
from collections import Counter
from sklearn.cluster import KMeans

In [255]:
# Число классов
countClasses = 3
# Число случайных величин
countVariables = 3
# Задаем объем обучающей выборки
countLearnDots = 10000
# Задаем объем контрольной выборки
countControlDots = 10
# Выбор срезов
x1 = 0
x2 = 1
# Задаем матрицы корелляции
correlations = [
    [
        [1, 0.7, 0],
        [0.7, 1, 0],
        [0, 0, 1]
    ], [
        [1, -0.23, 0],
        [-0.23, 1, 0],
        [0, 0, 1]
    ], [
        [1, 0, 0],
        [0, 1, 0],
        [0, 0, 1]
    ]
]
# Задаем вектора дисперсии
dispersions = [
    [1.0, 3.0, 0.5],
    [3.0, 1.0, 0.5],
    [4, 3, 1]
]
# Задаем вектора средних
means = [
    [7,  0.0, -0.89],
    [0.0,  -6.0,  0.89],
    [2.0, 6.0,  0.0]
]
# Задаем апостериорные вероятности
probabilities = [
    0.2, 0.5, 0.3
]
# Задаем интервалы для отрисовки поля
step = 0.1
# Задаем границы поля
x_min = -10
y_min = -10
width = 20
height = 20

In [256]:
def corToCov(cor, disp):
    cov = np.zeros((countVariables, countVariables))
    for i in range(countVariables):
        for j in range(countVariables):
            cov[i][j] = cor[i][j] * np.math.sqrt(disp[i] * disp[j])
    return cov

def generatePDF(mean, covariation):
    return np.array(list(map(multivariate_normal, mean, covariation)))
PDF_s = generatePDF(means, list(map(corToCov, correlations, dispersions)))

data_training_classes = np.random.choice(countClasses, countLearnDots, p=probabilities)
data_training_points = np.array([PDF_s[i].rvs() for i in data_training_classes])

data_control_classes = np.random.choice(countClasses, countControlDots, p=probabilities)
data_control_points = np.array([PDF_s[i].rvs() for i in data_control_classes])
# draw teaching dots
layout = go.Layout(
    width=1000,
    height=1000,
    xaxis=dict(
        range=[x_min, x_min + width]
    ),
    yaxis=dict(
        range=[y_min, y_min + width]
    )
)

data_training_points_transpose = data_training_points.transpose()
data_training_x1 = data_training_points_transpose[x1]
data_training_x2 = data_training_points_transpose[x2]
training_scatter = go.Scatter(
    x = data_training_x2,
    y = data_training_x1,
    mode = 'markers',
    name = "scatter",
    marker=dict(
        color = data_training_classes,
        colorscale=[[0.0, 'rgb(228,26,28)'], [0.25, 'rgb(55,126,184)'], [0.5, 'rgb(77,175,74)'], [0.75, 'rgb(152,78,163)'], [1.0, 'rgb(255,127,0)']],
    )
)

data_control_points_transpose = data_control_points.transpose()
data_control_x1 = data_control_points_transpose[x1]
data_control_x2 = data_control_points_transpose[x2]
control_scatter = go.Scatter(
    x = data_control_x2,
    y = data_control_x1,
    mode = 'markers',
    name = "scatter",
    marker=dict(
        color = data_control_classes,
        colorscale=[[0.0, 'rgb(228,26,28)'], [0.25, 'rgb(55,126,184)'], [0.5, 'rgb(77,175,74)'], [0.75, 'rgb(152,78,163)'], [1.0, 'rgb(255,127,0)']],
    )
)

fig_data = [training_scatter]
data = go.Figure(data = fig_data, layout = layout)
py.iplot(data)

In [257]:
def T_classifier(T):
    global data_training_classes
    global data_training_points
    global data_classify_classes
    map_classes = { 0: np.array([data_training_points[0]]) }
    classes_num = 1
    data_classify_classes[0] = 0
    for i in range(1, len(data_classify_classes)):
        p = data_training_points[i]
        dist = np.array([np.linalg.norm(map_classes[c].mean(0) - p) for c in range(classes_num)])
        min_class = np.argmin(dist)
        if (dist[min_class] <= T):
            map_classes[min_class] = np.append(map_classes[min_class], [p], axis=0)
            data_classify_classes[i] = min_class
        else:
            map_classes[classes_num] = np.array([p])
            data_classify_classes[i] = classes_num
            classes_num += 1

In [264]:
def maxMin_classifier():
    global data_training_classes
    global data_training_points
    global data_classify_classes

    center_index = np.zeros(len(data_training_points), dtype = np.int32)
    center = np.array([data_training_points[0]])
    z1_index = np.argmax(np.linalg.norm(data_training_points[1:] - data_training_points[0])) + 1
    center_index[1] = z1_index
    center = np.append(center, [data_training_points[z1_index]], axis=0)
    center_count = 2
    mean_dist = np.linalg.norm(center[0] - center[1])

    while True:
        dist_all = np.zeros(len(data_training_points))
        for i in range(len(data_training_points)):
            dist = np.zeros(center_count)
            for j in range(center_count):
                dist[j] = np.linalg.norm(data_training_points[i] - center[j])
            dist_all[i] = dist.min()
        z_index = np.argmax(dist_all)
        dist_max = dist_all[z_index]
        if dist_max > mean_dist * 0.6:
            center = np.append(center, [data_training_points[z_index]], axis=0)
            center_index[center_count] = z_index
            mean_dist = (mean_dist * (center_count - 1) + dist_max) / center_count
            center_count += 1
        else:
            break
    for i in range(len(data_training_points)):
        dist = np.zeros(center_count)
        for j in range(center_count):
            dist[j] = np.linalg.norm(data_training_points[i] - center[j])
        data_classify_classes[i] = dist.argmin()

In [259]:
def K_classifier(K):
    global data_training_classes
    global data_training_points
    global data_classify_classes

    kmeans = KMeans(n_clusters=K).fit(data_training_points)
    data_classify_classes = kmeans.labels_
    kmeans.cluster_centers_

In [260]:
def print_stats():
    s = ""

    c = Counter(data_training_classes)
    class_counter_real = len(c)

    c = Counter(data_classify_classes)
    class_counter = len(c)

    s += "Число классов: " + str(class_counter) + "\n"
    s += "Кол-во элементов в классе:\n"
    for i in range(class_counter):
        s += str(i) + " = " + str(c[i]) + "\n"

    transform_matrix = np.zeros((class_counter_real, class_counter), dtype=np.int64)
    for i in np.arange(len(data_classify_classes)):
        class_real = data_training_classes[i]
        class_pred = data_classify_classes[i]
        # print(class_real, class_pred)
        transform_matrix[class_real][class_pred] += 1
    s += "Матрица трансформации:\n" + np.array_str(transform_matrix.transpose()) + "\n"

    classes_center_map = {}
    for i in range(len(data_classify_classes)):
        if data_classify_classes[i] in classes_center_map:
            classes_center_map[data_classify_classes[i]] += data_training_points[i]
        else:
            classes_center_map[data_classify_classes[i]] = np.copy(data_training_points[i])
    for i in range(class_counter):
        classes_center_map[i] = classes_center_map[i] / c[i]
    center = np.array([classes_center_map[i] for i in range(class_counter)])
    s += "Координаты центров:\n" + np.array_str(center) + "\n"

    center_dist = np.zeros((class_counter, class_counter))
    for i in range(class_counter):
        for j in range(class_counter):
            center_dist[i][j] = np.linalg.norm(classes_center_map[i] - classes_center_map[j])
    s += "Расстояние между центрами:\n" + np.array_str(center_dist) + "\n"

    classes_disp_map = {}
    for i in range(len(data_classify_classes)):
        if data_classify_classes[i] in classes_disp_map:
            classes_disp_map[data_classify_classes[i]] += np.power(data_training_points[i] - classes_center_map[data_classify_classes[i]], 2)
        else:
            classes_disp_map[data_classify_classes[i]] = np.power(data_training_points[i] - classes_center_map[data_classify_classes[i]], 2)

    for i in range(class_counter):
        classes_disp_map[i] = np.sqrt(classes_disp_map[i] / c[i])
    disp = np.array([classes_disp_map[i] for i in range(class_counter)])
    s += "Среднеквадратические разбросы признаков:\n" + np.array_str(disp) + "\n"


    int_cr = 0.0
    for i in range(len(data_classify_classes)):
        int_cr += np.linalg.norm(data_training_points[i] - classes_center_map[data_classify_classes[i]])
    s += "Интегральный критерий: " + str(int_cr) + "\n"

    return s

In [262]:
data_classify_classes = np.zeros(data_training_classes.size, dtype=np.int32)

T = 9
T_classifier(T)

layout = go.Layout(
    width=1000,
    height=1000,
    xaxis=dict(
        range=[x_min, x_min + width]
    ),
    yaxis=dict(
        range=[y_min, y_min + width]
    )
)

data_training_points_transpose = data_training_points.transpose()
data_training_x1 = data_training_points_transpose[x1]
data_training_x2 = data_training_points_transpose[x2]
training_scatter = go.Scatter(
    x = data_training_x2,
    y = data_training_x1,
    mode = 'markers',
    name = "scatter",
    marker=dict(
        color = data_classify_classes,# data_training_classes
        colorscale=[[0.0, 'rgb(228,26,28)'], [0.25, 'rgb(55,126,184)'], [0.5, 'rgb(77,175,74)'], [0.75, 'rgb(152,78,163)'], [1.0, 'rgb(255,127,0)']],
    )
)

data_control_points_transpose = data_control_points.transpose()
data_control_x1 = data_control_points_transpose[x1]
data_control_x2 = data_control_points_transpose[x2]
control_scatter = go.Scatter(
    x = data_control_x2,
    y = data_control_x1,
    mode = 'markers',
    name = "scatter",
    marker=dict(
        color = data_control_classes,
        colorscale=[[0.0, 'rgb(228,26,28)'], [0.25, 'rgb(55,126,184)'], [0.5, 'rgb(77,175,74)'], [0.75, 'rgb(152,78,163)'], [1.0, 'rgb(255,127,0)']],
    )
)

fig_data = [training_scatter]
data = go.Figure(data = fig_data, layout = layout)
py.iplot(data)
print(print_stats())

Число классов: 3
Кол-во элементов в классе:
0 = 5021
1 = 2890
2 = 2089
Матрица трансформации:
[[   5 5013    3]
 [   0    0 2890]
 [2022    1   66]]
Координаты центров:
[[ 0.01607442 -6.01139526  0.88241809]
 [ 1.86697242  6.06094268 -0.03868714]
 [ 6.97180635  0.11977825 -0.87863375]]
Расстояние между центрами:
[[ 0.         12.24808563  9.43794462]
 [12.24808563  0.          7.87796132]
 [ 9.43794462  7.87796132  0.        ]]
Среднеквадратические разбросы признаков:
[[1.73798295 1.00515222 0.71000978]
 [1.93690712 1.67639402 1.00990075]
 [1.06274372 1.76623229 0.7222901 ]]
Интегральный критерий: 20861.475624487917



In [265]:
data_classify_classes = np.zeros(data_training_classes.size, dtype=np.int32)

maxMin_classifier()
# MaxMin classifier

layout = go.Layout(
    width=1000,
    height=1000,
    xaxis=dict(
        range=[x_min, x_min + width]
    ),
    yaxis=dict(
        range=[y_min, y_min + width]
    )
)

data_training_points_transpose = data_training_points.transpose()
data_training_x1 = data_training_points_transpose[x1]
data_training_x2 = data_training_points_transpose[x2]
training_scatter = go.Scatter(
    x = data_training_x2,
    y = data_training_x1,
    mode = 'markers',
    name = "scatter",
    marker=dict(
        color = data_classify_classes,
        colorscale=[[0.0, 'rgb(228,26,28)'], [0.25, 'rgb(55,126,184)'], [0.5, 'rgb(77,175,74)'], [0.75, 'rgb(152,78,163)'], [1.0, 'rgb(255,127,0)']],
    )
)

data_control_points_transpose = data_control_points.transpose()
data_control_x1 = data_control_points_transpose[x1]
data_control_x2 = data_control_points_transpose[x2]
control_scatter = go.Scatter(
    x = data_control_x2,
    y = data_control_x1,
    mode = 'markers',
    name = "scatter",
    marker=dict(
        color = data_control_classes,
        colorscale=[[0.0, 'rgb(228,26,28)'], [0.25, 'rgb(55,126,184)'], [0.5, 'rgb(77,175,74)'], [0.75, 'rgb(152,78,163)'], [1.0, 'rgb(255,127,0)']],
    )
)

fig_data = [training_scatter]
data = go.Figure(data = fig_data, layout = layout)
py.iplot(data)
print(print_stats())

Число классов: 3
Кол-во элементов в классе:
0 = 5002
1 = 2850
2 = 2148
Матрица трансформации:
[[   0 5000    2]
 [   0    0 2850]
 [2027   14  107]]
Координаты центров:
[[ 3.01888148e-04 -6.01701382e+00  8.84647951e-01]
 [ 1.83503973e+00  6.10081498e+00 -3.25274169e-02]
 [ 6.89431572e+00  1.36362163e-01 -8.60780475e-01]]
Расстояние между центрами:
[[ 0.         12.29020945  9.40414712]
 [12.29020945  0.          7.86492048]
 [ 9.40414712  7.86492048  0.        ]]
Среднеквадратические разбросы признаков:
[[1.72120759 0.99999175 0.70803803]
 [1.92513213 1.64923003 1.00999077]
 [1.16285195 1.85402989 0.73842121]]
Интегральный критерий: 20906.72159745078



In [266]:
data_classify_classes = np.zeros(data_training_classes.size, dtype=np.int32)

K = 3

# K averages
K_classifier(K)

layout = go.Layout(
    width=1000,
    height=1000,
    xaxis=dict(
        range=[x_min, x_min + width]
    ),
    yaxis=dict(
        range=[y_min, y_min + width]
    )
)

data_training_points_transpose = data_training_points.transpose()
data_training_x1 = data_training_points_transpose[x1]
data_training_x2 = data_training_points_transpose[x2]
training_scatter = go.Scatter(
    x = data_training_x2,
    y = data_training_x1,
    mode = 'markers',
    name = "scatter",
    marker=dict(
        color = data_classify_classes,
        colorscale=[[0.0, 'rgb(228,26,28)'], [0.25, 'rgb(55,126,184)'], [0.5, 'rgb(77,175,74)'], [0.75, 'rgb(152,78,163)'], [1.0, 'rgb(255,127,0)']],
    )
)

data_control_points_transpose = data_control_points.transpose()
data_control_x1 = data_control_points_transpose[x1]
data_control_x2 = data_control_points_transpose[x2]
control_scatter = go.Scatter(
    x = data_control_x2,
    y = data_control_x1,
    mode = 'markers',
    name = "scatter",
    marker=dict(
        color = data_control_classes,
        colorscale=[[0.0, 'rgb(228,26,28)'], [0.25, 'rgb(55,126,184)'], [0.5, 'rgb(77,175,74)'], [0.75, 'rgb(152,78,163)'], [1.0, 'rgb(255,127,0)']],
    )
)

fig_data = [training_scatter]
data = go.Figure(data = fig_data, layout = layout)
py.iplot(data)
print(print_stats())

Число классов: 3
Кол-во элементов в классе:
0 = 2894
1 = 5020
2 = 2086
Матрица трансформации:
[[   0    0 2894]
 [   5 5013    2]
 [2022    1   63]]
Координаты центров:
[[ 1.86940585  6.05608092 -0.03807493]
 [ 0.01596815 -6.01264087  0.88211977]
 [ 6.97514036  0.11518912 -0.87953162]]
Расстояние между центрами:
[[ 0.         12.24483709  7.87850047]
 [12.24483709  0.          9.43842116]
 [ 7.87850047  9.43842116  0.        ]]
Среднеквадратические разбросы признаков:
[[1.93793912 1.68116342 1.01034462]
 [1.73813973 1.00137    0.7097658 ]
 [1.05950829 1.76319942 0.72219308]]
Интегральный критерий: 20860.685951513347

